In [1]:
import torch
import pickle
import numpy as np
import os.path as osp
import numpy as np
import torch
from torch_geometric.data import Data, InMemoryDataset
from torch_geometric.loader import DataLoader
from torch_geometric.datasets import TUDataset, zinc, QM7b, ModelNet
from torch_geometric.utils import (
    to_networkx,
    homophily,
    erdos_renyi_graph,
    stochastic_blockmodel_graph,
    scatter,
    loop,
)
from torch_geometric.nn import GINConv, global_mean_pool, global_add_pool
from torch_geometric.nn.aggr import (
    DeepSetsAggregation,
)  # key to implement DeepSet input (batch_features, batch_index)
from torch_geometric.nn.models import MLP
import torch.nn as nn
from torch.nn import Linear, Sequential, ReLU, Dropout
import torch_geometric.transforms as T
import torch.nn.functional as F
from torch.optim import SGD
from tqdm.auto import tqdm

from sklearn.model_selection import KFold
from sklearn.model_selection import train_test_split
from sklearn.cluster import KMeans
import os
os.environ["CUDA_VISIBLE_DEVICES"] = "2"
data_dir =  "/export/canton/data/yma93/anydim_transferability/OI-DS/"


/cis/home/yma93/miniconda3/envs/ml/lib/python3.9/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


In [14]:
xtrain, ytrain, xval, yval = pickle.load(
    open(f"{data_dir}/ModelNet_np_100.pkl", "rb")
)
xtrain

[array([[-0.5109236 ,  0.11919375,  0.25615597],
        [ 0.31158122, -0.2834755 , -0.1012808 ],
        [ 0.21475756,  0.32269573, -0.23091409],
        [-0.16616179, -0.62841386, -0.10645141],
        [-0.21032266, -0.5297847 , -0.09550686],
        [ 0.17532896,  0.3235343 , -0.21528374],
        [ 0.05248746,  0.8202656 ,  0.04768752],
        [ 0.46502241, -0.05671944,  0.10810165],
        [-0.00190719, -0.6606134 , -0.12572767],
        [ 0.4930932 ,  0.2988775 ,  0.20083529],
        [ 0.38320118, -0.04119327, -0.05111989],
        [-0.2972788 ,  0.65607214,  0.02062805],
        [ 0.4500997 , -0.23899403,  0.11979488],
        [ 0.04828098,  0.3897514 , -0.21528374],
        [-0.30908734,  0.24552312, -0.13080122],
        [ 0.27628604,  0.81322217,  0.21340214],
        [ 0.46110848, -0.26317027,  0.21607181],
        [-0.05589807, -0.56686425, -0.16601413],
        [ 0.19279476, -0.50924236, -0.14255573],
        [-0.35729071,  0.40271074, -0.04605228],
        [-0.18301003

# Data

In [5]:
from train import OIDSTrainingModule
params = {
    "data_dir": "/export/canton/data/yma93/anydim_transferability/OI-DS/",
    "model": {
        "out_channels": 10,
        "hidden_channels": 30,
    },
}
model = OIDSTrainingModule(params)
model.prepare_data()

/cis/home/yma93/projects/Anydim_transferability/O(n)/train.py:194: UserWarning: Creating a tensor from a list of numpy.ndarrays is extremely slow. Please consider converting the list to a single numpy.ndarray with numpy.array() before converting to a tensor. (Triggered internally at /opt/conda/conda-bld/pytorch_1670525551200/work/torch/csrc/utils/tensor_new.cpp:230.)
  torch.tensor(xtrain_s),


In [6]:
def sample_pointclouds(xtrain, ytrain, xval, yval, classes, num_pointclouds, num_pointclouds_test):
    xtrain_s = []
    ytrain_s = []
    xtest_s = []
    ytest_s = []
    idxs_out = []
    idxs_out_test = []
    for i in classes:
        indices = [s for s in range(len(ytrain)) if ytrain[s] == i]
        indices_test = [s for s in range(len(yval)) if yval[s] == i]
        # indices = slice(*idxs[0:num_pointclouds])
        if num_pointclouds == -1 or num_pointclouds > len(indices):
            num_pointclouds = len(indices)
        if num_pointclouds_test == -1 or num_pointclouds_test > len(indices_test):
            num_pointclouds_test = len(indices_test)
        for s in range(num_pointclouds):
            xtrain_s.append(xtrain[indices[s]])
            ytrain_s.append(ytrain[indices[s]])
            idxs_out = indices[s]
        for s in range(num_pointclouds_test):
            xtest_s.append(xval[indices_test[s]])
            ytest_s.append(yval[indices_test[s]])
            idxs_out_test = indices_test[s]
    return xtrain_s, ytrain_s, xtest_s, ytest_s, idxs_out, idxs_out_test

In [7]:
data = pickle.load(open(f"{data_dir}/ModelNet_np_withLabels_pts=100.pkl", "rb"))
classes = [2, 7]
num_pointclouds = 40
epsilon = 0.01
print(data["train_pos"][0].shape)
xtrain_s, ytrain_s, xtest_s, ytest_s, indices, indices_test = sample_pointclouds(
    data["train_pos"],
    data["train_y"],
    data["val_pos"],
    data["val_y"],
    classes,
    num_pointclouds,
    num_pointclouds,
)
# total_points, total_weights = segment.segment_point_cloud(
#     jnp.concatenate(xtrain_s + xtest_s),
#     num_per_segment=[cloud.shape[0] for cloud in xtrain_s + xtest_s],
# )
# print(len(xtrain_s), len(xtest_s), len(xtrain_s + xtest_s))

# print(len(xtrain_s), len(xtest_s), len(xtrain_s + xtest_s))

(100, 3)


In [9]:
len(ytrain_s)

80

In [ ]:
len(xtrain_s)

In [5]:
dist_true_train = pickle.load(open(data_dir+"LB_GW_train.pkl", "rb"))
dist_true_train = torch.from_numpy(np.array(dist_true_train)).unsqueeze(1)
dist_true_test = pickle.load(open(data_dir+"LB_GW_test.pkl", "rb"))
dist_true_test = torch.from_numpy(np.array(dist_true_test)).unsqueeze(1)

In [7]:
dist_true_train

tensor([[0.1123],
        [0.0816],
        [0.0776],
        ...,
        [0.3235],
        [0.1228],
        [0.4604]])

In [ ]:
def get_fs(X):
    """
    input: X (n by 3)
    output: Data (class) storing fs (n by (n + n(n-1)/2 + 1)) feature matrix
     f_d is the set of diagonal edge attributes,
     f_o is the set of off-diagonal (upper) edge attributes,
     f_star is \sum_{i \neq j} X_ii X_ij where X is the n by n edge attribute graph
    """
    n = X.shape[0]
    data = Data()
    Gram = torch.FloatTensor(X @ X.T)
    off_mask = torch.triu(torch.ones(n, n)) == 1

    data.f_d = torch.diagonal(Gram, 0).unsqueeze(1)
    data.f_o = Gram[off_mask].unsqueeze(1)
    data.f_star = (
        (data.f_d * (torch.sum(Gram, dim=1, keepdim=True) - data.f_d)).sum().reshape((1, 1))
    )

    return data


def get_Kmeans(X, k=3):
    """
    Implement eqn 6: replace f_d as the self-dots of the K-means dots
    input: X (n by 3), k: number of k-means clusters
    output: Data (class) storing  feature matrix
     f_d is the flattened feature of the gram matrix of K-means centroids
     f_o is the set of dot products of each point to the K-means centroids
    """
    n = X.shape[0]
    data = Data()

    kmeans = KMeans(n_clusters=k, random_state=0, init="k-means++", n_init=1).fit(X)
    K = kmeans.cluster_centers_  # (num_centroids, 3)
    # sort Kmeans centroid by norm
    indexlist = np.argsort(np.linalg.norm(K, axis=1))
    K = K[indexlist, :]
    data.f_o = torch.FloatTensor(X @ K.T)  # shape(n, d)
    Gram_k = torch.FloatTensor(K @ K.T)  # shape (d, d)
    data.f_d = Gram_k.reshape(1, k * k)  # shape (d^2,)
    return data

In [ ]:
def build_dataset(xtrain_s, xtest_s, ids, Kmeans=False, k=3):
    X_train = []
    X_test = []
    for i in ids:
        if Kmeans:
            X_train.append(get_Kmeans(xtrain_s[i], k=k))
            X_test.append(get_Kmeans(xtest_s[i], k=k))
        else:
            X_train.append(get_fs(xtrain_s[i]))
            X_test.append(get_fs(xtest_s[i]))

    return X_train, X_test


def get_loaders(train_data1, test_data1, train_data2, test_data2, batch_size, follow_batch=None):
    """
    data1, data2 refers to subsets in ModelNet10 belonging to two different classes
    """

    train_loader1 = DataLoader(
        train_data1, batch_size=batch_size, shuffle=False, follow_batch=follow_batch
    )
    train_loader2 = DataLoader(
        train_data2, batch_size=batch_size, shuffle=False, follow_batch=follow_batch
    )

    test_loader1 = DataLoader(
        test_data1, batch_size=batch_size, shuffle=False, follow_batch=follow_batch
    )

    test_loader2 = DataLoader(
        test_data2, batch_size=batch_size, shuffle=False, follow_batch=follow_batch
    )
    print(len(train_loader1), len(train_loader2), len(test_loader1), len(test_loader2))

    return train_loader1, train_loader2, test_loader1, test_loader2

In [ ]:
idx1 = np.where(np.array(ytrain_s) == 2)[0]
idx2 = np.where(np.array(ytrain_s) == 7)[0]
X_train1, X_test1 = build_dataset(xtrain_s, xtest_s, idx1)
X_train2, X_test2 = build_dataset(xtrain_s, xtest_s, idx2)

In [ ]:
len(idx1), len(X_train1)

In [ ]:
n_train = len(xtrain_s)
n_test = len(xtest_s)
bs = 40
train_loader1, train_loader2, test_loader1, test_loader2 = get_loaders(
    X_train1, X_test1, X_train2, X_test2, batch_size=bs, follow_batch=["f_d", "f_o"]
)

In [ ]:
len(train_loader1.dataset)

# Scalar Model

In [ ]:
class ScalarModel(torch.nn.Module):
    def __init__(self, hid_dim, out_dim, dropout=0, input_dim=1, input_off=1):
        '''
        For all off-diag scalars, input_off = 1
        '''
        super(ScalarModel, self).__init__()
        #Deepset for diagonal scalars
        phi_d = MLP([input_dim,hid_dim, hid_dim*2], dropout=[dropout]*2)
        rho_d = MLP([hid_dim*2, hid_dim], dropout=[dropout]*1) #MLP([hid_dim*2, hid_dim, hid_dim], dropout=[dropout]*2) #
        self.deepset_d = DeepSetsAggregation(local_nn=phi_d, global_nn=rho_d)
        #Deepset for off-diagonal scalars
        phi_o = MLP([input_off,hid_dim, hid_dim*2], dropout=[dropout]*2)
        rho_o = MLP([hid_dim*2, hid_dim], dropout=[dropout]*1) #MLP([hid_dim*2, hid_dim, hid_dim], dropout=[dropout]*2)
        self.deepset_o = DeepSetsAggregation(local_nn=phi_o, global_nn=rho_o)
        #MLP_s for f_star
        self.MLP_s = MLP([input_dim,hid_dim, hid_dim], dropout=[dropout]*2)  #MLP([1,hid_dim*2, hid_dim], dropout=[dropout]*2) #
        #MLP for (Deepset(f_d), Deepset(f_o), f_star)
        self.MLP_out = MLP([hid_dim*3, hid_dim, out_dim], dropout=[dropout]*2)
        self.out_dim = out_dim

    def reset_parameters(self):
        for net in [self.deepset_d, self.deepset_o, self.MLP_s, self.MLP_out]:
        #for net in [self.deepset_d, self.deepset_o, self.MLP_out]:
            net.reset_parameters()

    def forward(self, data):
        out_d = self.deepset_d(data.f_d, data.f_d_batch) # bs x hid_dim
        out_o = self.deepset_o(data.f_o, data.f_o_batch) # bs x hid_dim
        out_star = self.MLP_s(data.f_star) #bs x hid_dim
        #concat and output final embedding
        out = self.MLP_out(torch.concat([out_d, out_o, out_star], dim=-1)) # bs x hid_dim*3 -> bs x out_dim
        return out

In [ ]:
from torchmetrics.functional.pairwise import pairwise_euclidean_distance
from torchmetrics.regression import SpearmanCorrCoef

class ScalarModel_KMeans(torch.nn.Module):
    def __init__(self, hid_dim, out_dim, dropout=0, input_dim=9, input_off=3):
        """
        input_dim = d^2
        input_off = d
        """
        super(ScalarModel_KMeans, self).__init__()
        # MLP for k-means gram matrix, C(Y) C(Y)^T
        self.MLP_km = MLP([input_dim, input_dim * 2, hid_dim], dropout=[dropout] * 2)
        # Deepset for k-means features, C(Y) Y (action on the n points in R^d)
        phi_o = MLP([input_off, hid_dim, hid_dim * 2], dropout=[dropout] * 2)
        rho_o = MLP(
            [hid_dim * 2, hid_dim], dropout=[dropout] * 1
        )  # MLP([hid_dim*2, hid_dim, hid_dim], dropout=[dropout]*2)
        self.deepset_o = DeepSetsAggregation(local_nn=phi_o, global_nn=rho_o)
        # MLP for (MLP_km(f_km), Deepset(f_d))
        self.MLP_out = MLP([hid_dim * 2, hid_dim, out_dim], dropout=[dropout] * 2)
        self.out_dim = out_dim

    def reset_parameters(self):
        for net in [self.MLP_km, self.deepset_o, self.MLP_out]:
            net.reset_parameters()

    def forward(self, data):
        out_d = self.MLP_km(data.f_d, data.f_d_batch)  # bs x hid_dim
        out_o = self.deepset_o(data.f_o, data.f_o_batch)  # bs x hid_dim
        # concat and output final embedding
        out = self.MLP_out(torch.concat([out_d, out_o], dim=-1))  # bs x hid_dim*2 -> bs x out_dim
        return out


# cf: metric learning https://en.wikipedia.org/wiki/Similarity_learning
class SiameseRegressor(torch.nn.Module):
    def __init__(self, ScalarModel):
        super(SiameseRegressor, self).__init__()
        self.SM = ScalarModel
        # metric learning (TODO: should we do this for the GW dist instead?)
        self.metric = nn.Linear(self.SM.out_dim, self.SM.out_dim, bias=False)
        self.metric.reset_parameters()
        self.linear = nn.Linear(1, 1)
        self.linear.reset_parameters()

    def forward(self, x1, x2):
        n = x1.num_graphs
        emb1 = self.SM(x1)  # n by out_dim
        emb2 = self.SM(x2)  # n by out_dim
        emb1 = self.metric(emb1)  # project
        emb2 = self.metric(emb2)  # project
        dist_mat = pairwise_euclidean_distance(emb1, emb2)  # n by n matrix
        dist_vec = dist_mat.flatten().unsqueeze(1)
        dist_pred = self.linear(dist_vec)
        return dist_pred


def train(model, optimizer, criterion, loader1, loader2, dist_true):
    model.train()

    total_loss = 0
    for data1, data2 in zip(loader1, loader2):
        data1 = data1.to(device)
        data2 = data2.to(device)
        optimizer.zero_grad()  # Clear gradients.
        dist_pred = model(data1, data2)  # Forward pass.
        loss = criterion(dist_pred, dist_true)  # Loss computation.
        loss.backward()  # Backward pass.
        optimizer.step()  # Update model parameters.
        total_loss += loss.item()

    return total_loss / len(loader1)


@torch.no_grad()
def test(model, criterion, loader1, loader2, dist_true):
    model.eval()

    total_loss = 0
    for data1, data2 in zip(loader1, loader2):
        data1 = data1.to(device)
        data2 = data2.to(device)
        dist_pred = model(data1, data2)  # Forward pass.
        loss = criterion(dist_pred, dist_true)  # Loss computation.
        total_loss += loss.item()

    return total_loss / len(loader1)

In [ ]:
hid_dim = 16
out_dim = 16
scalar = ScalarModel(hid_dim, out_dim, input_dim=1)
model = SiameseRegressor(scalar)
model = model.to(device)
print(model)

model.SM.reset_parameters()
# optimizer = torch.optim.Adam(model.parameters(), lr=0.001)
optimizer = torch.optim.Adam(
    [
        {"params": model.SM.parameters()},
        {"params": model.metric.parameters(), "lr": 1e-2},
        {"params": model.linear.parameters(), "lr": 1e-2},
    ],
    lr=1e-3,
)
criterion = torch.nn.MSELoss()  # Define loss criterion.

for epoch in range(1, 201):
    train_loss = train(
        model, optimizer, criterion, train_loader1, train_loader2, dist_true_train.to(device)
    )
    # scheduler.step(loss)
    test_loss = test(model, criterion, test_loader1, test_loader2, dist_true_test.to(device))
    if epoch % 10 == 0:
        print(f"Epoch: {epoch:02d}, Loss: {train_loss:.4f}, Test Loss: {test_loss:.4f}")

In [ ]:
def evaluate_dist_mat(model, loader1, loader2):
    model.eval()
    data1 = next(iter(loader1)).to(device)
    data2 = next(iter(loader2)).to(device)
    dist_vec = model(data1, data2).detach().cpu()
    n = data1.num_graphs
    dist_mat = torch.unflatten(dist_vec, 0, (n, n))
    return dist_mat

In [ ]:
D_pred_train = evaluate_dist_mat(model, train_loader1, train_loader2)
D_pred_test = evaluate_dist_mat(model, test_loader1, test_loader2)

In [ ]:
spearman = SpearmanCorrCoef()
rank_corr_train = spearman(D_pred_train.reshape(-1, 1), dist_true_train)
rank_corr_test = spearman(D_pred_test.reshape(-1, 1), dist_true_test)
rank_corr_train, rank_corr_test